In [4]:
import os
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import statsmodels.api as sm
import plotly.graph_objects as go
import numpy as np
from pandas_datareader import data as wb
import plotly.express as px
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

/Users/danvaldes/anaconda3/lib/python3.7/site-packages/pandas_datareader/compat/__init__.py:7: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



In [3]:
# from pandas_profiling import ProfileReport

In [4]:
# profile = ProfileReport(df, title='Pandas Profiling Report', html={'style':{'full_width':True}})

Pandas display options to supress scientifc notation and show all columns and all rows if necessary. Puts a lot of strain of processor

In [5]:
# pd.options.display.max_columns = None
# pd.options.display.max_rows = None
pd.options.display.float_format= '{:.2f}'.format

In [6]:
nyse = pd.read_csv(os.path.join('Resources', 'nyse.csv'))
nasdaq = pd.read_csv(os.path.join('Resources', 'nasdaq.csv'))
amex = pd.read_csv(os.path.join('Resources', 'amex.csv'))

frames = [nyse, nasdaq, amex]
tickers = pd.concat(frames).sort_values(by='Ticker')

In [7]:
data_2018 = pd.read_csv(os.path.join('Resources', '2018_Financial_Data.csv')).\
rename(columns={'Unnamed: 0':'Ticker'}).\
sort_values(by='Ticker').\
reset_index(drop=True)

df = tickers.merge(data_2018, on='Ticker')

df['Market Cap Size'] = ['Large Cap' if x > 10000000000 else 'Mid Cap' if x > 2000000000 else 'Small Cap' for x in df['Market Cap']]

Note: In *__data_2018__* we had 4392 observations. When we merged with our *__tickers__* dataframe which had 8000+ tickers and company names from exchanges we lost 150 observations. These can be retrieved with 
``` 
data_2018[~data_2018.Ticker.isin(tickers['Ticker'])]
```
Here the **~** symbol essentially means NOT IN when we filter.\
Lastly, a dataframe with just indicators we can manipulate. We can filter out some of the columns containing information we don't need then pass this as a filter to our working dataframe with ```df[x['Indicator']]```

In [ ]:
indicators = pd.DataFrame({
   'Indicator': df.iloc[:,2:-2].columns.tolist()
})

In [ ]:
x = indicators[indicators['Indicator'].str.contains('Growth|Margin|growth|ratio|Ratio|Turnover|per|/| / | to |Per|return|To|days') == False]

cond = x['Indicator'].to_list()
cond;

In [ ]:
len(cond);

In [ ]:
df.fillna(0);

In [18]:
small_caps = df[df['Market Cap Size'] == 'Small Cap']
mid_caps = df[df['Market Cap Size'] == 'Mid Cap']
large_caps = df[df['Market Cap Size'] == 'Large Cap']

## Conditional Filtering

In [12]:
tickers[tickers['Ticker'].str.startswith('BA') == True];

In [14]:
tickers[tickers['Company Name'].str.contains('ETF') == True];

In [16]:
df[df['Company Name'].str.contains('ETF') == True];

In [30]:
df[df['Ticker'].str.startswith('BA') == True];

In [ ]:
df[df['Revenue Growth'] > 10].sort_values(by='Revenue', ascending=False).head()

# Iterators 

Sector breakdown across Market Cap Sizes

In [ ]:
count = pd.DataFrame(df.groupby(['Market Cap Size'])['Sector'].value_counts());

count_gen = count.groupby(['Market Cap Size']).__iter__()

In [ ]:
count_group_id, count_grouped_data = count_gen.__next__()
print(count_group_id) 
count_grouped_data

Iterate across Market Caps and Sectors

In [ ]:
mcap_gen = df.groupby(['Market Cap Size']).__iter__()
sector_gen = df.groupby(['Sector']).__iter__()

In [ ]:
market_group_id, market_grouped_data = mcap_gen.__next__()
print(market_group_id) 
market_grouped_data;

In [ ]:
sector_group_id, sector_grouped_data = sector_gen.__next__()
print(sector_group_id)
sector_grouped_data;

In [19]:
scap_gen = small_caps.groupby(['Sector']).__iter__()

In [127]:
scap_group_id, scap_grouped_data = scap_gen.__next__()
print(scap_group_id) 
scap_grouped_data.sort_values(by='Revenue Growth', ascending=False)

Energy


Ticker                              Company Name       Revenue  \
3261   ROSE                    Rosehill Resources Inc  301875000.00   
1880   HUSA              Houston American Energy Corp    2356660.00   
2253   LLEX                          Lilis Energy Inc   70216000.00   
2690    NOG                      Northern Oil and Gas  678924496.00   
3509    SOI  Solaris Oilfield Infrastructure Inc Cl A  197196000.00   
...     ...                                       ...           ...   
2953    PER                   Sandridge Permian Trust   30000000.00   
3263   ROYT                   Pacific Coast Oil Trust          0.00   
3342    SBR                      Sabine Royalty Trust   53000000.00   
3368   SDRL                              Seadrill Ltd 2045000000.00   
4015    VOC                          Voc Energy Trust   13000000.00   

      Revenue Growth  Cost of Revenue  Gross Profit  R&D Expenses  \
3261            2.96      58455000.00  243420000.00    4374000.00   
1880            2.74        914269.00    1442391.00          0.00   
2253            2.25      20944000.00   49272000.00          0.00   
2690            2.24     111947972.00  566976524.00          0.00   
3509            1.93      60902000.00  136294000.00          0.00   
...              ...              ...           ...           ...   
2953             nan       1000000.00   28000000.00           nan   
3263             nan       1000000.00   -1000000.00           nan   
3342             nan              nan   53000000.00           nan   
3368             nan     792000000.00  461000000.00          0.00   
4015             nan             0.00   13000000.00           nan   

      SG&A Expense  Operating Expenses  Operating Income  ...  \
3261   30469000.00        177157000.00       66263000.00  ...   
1880    1422560.00          1780382.00        -337991.00  ...   
2253   33251000.00         58618000.00       -9346000.00  ...   
2690   14568362.00        134348037.00      432628487.00  ...   
3509   16758000.00         37007000.00       99287000.00  ...   
...            ...                 ...               ...  ...   
2953    1000000.00                 nan               nan  ...   
3263    2000000.00                 nan               nan  ...   
3342    3000000.00                 nan               nan  ...   
3368  191000000.00       1532000000.00     -355000000.00  ...   
4015    1000000.00                 nan               nan  ...   

      Inventory Growth  Asset Growth  Book Value per Share Growth  \
3261              0.00          0.71                         0.01   
1880              0.00          0.03                        -0.07   
2253              0.00          1.45                         1.29   
2690              0.00          1.38                         1.23   
3509              0.39          0.53                         0.62   
...                ...           ...                          ...   
2953               nan           nan                          nan   
3263               nan           nan                          nan   
3342               nan           nan                          nan   
3368              0.00         -0.06                          nan   
4015               nan           nan                          nan   

      Debt Growth  R&D Expense Growth  SG&A Expenses Growth  Sector  \
3261         2.09                1.50                  1.27  Energy   
1880         0.00                0.00                 -0.33  Energy   
2253        -0.21                0.00                 -0.33  Energy   
2690        -0.16                0.00                 -0.23  Energy   
3509        61.21                0.00                  0.17  Energy   
...           ...                 ...                   ...     ...   
2953          nan                 nan                   nan  Energy   
3263          nan                 nan                   nan  Energy   
3342          nan                 nan                   nan  Energy   
336

In [124]:
assets = scap_grouped_data['Ticker'].to_list()

pf_data = pd.DataFrame()

for a in assets:
    pf_data[a] = wb.DataReader(a, data_source = 'yahoo', start = '2018-1-1')['Adj Close']

(pf_data / pf_data.iloc[0] * 100).iplot(asFigure=True)

In [128]:
mcap_gen = mid_caps.groupby(['Sector']).__iter__()

In [129]:
mcap_group_id, mcap_grouped_data = mcap_gen.__next__()
print(mcap_group_id) 
mcap_grouped_data.sort_values(by='Revenue Growth', ascending=False)

Basic Materials


Ticker                     Company Name        Revenue  Revenue Growth  \
1477    FMC                         FMC Corp  4727800000.00            0.64   
1550    FUL             H. B. Fuller Company  3041002000.00            0.32   
2400   MEOH                      Methanex Cp  3931847000.00            0.28   
817     CLF             Cleveland-Cliffs Inc  2332400000.00            0.25   
3589   STLD               Steel Dynamics Inc 11821839000.00            0.24   
3787   TREX                     Trex Company   684250000.00            0.21   
843     CMC        Commercial Metals Company  4643723000.00            0.21   
673     CBT                       Cabot Corp  3242000000.00            0.19   
3862     TX                     Ternium S.A. 11455000000.00            0.18   
2649   NGVT                    Ingevity Corp  1133600000.00            0.17   
4167      X         United States Steel Corp 14178000000.00            0.16   
1        AA                       Alcoa Corp 13403000000.00            0.15   
300     ASH      Ashland Global Holdings Inc  3743000000.00            0.15   
1366    EXP              Eagle Materials Inc  1386520000.00            0.14   
1691    GRA             W.R. Grace & Company  1932100000.00            0.13   
1877    HUN                    Huntsman Corp  9379000000.00            0.12   
285    ARLP             Alliance Resource Pt  2002857000.00            0.12   
2823    OLN                        Olin Corp  6946100000.00            0.11   
2790     OC                Owens Corning Inc  7057000000.00            0.11   
153     ALB                   Albemarle Corp  3374950000.00            0.10   
3037    POL                     Polyone Corp  3533400000.00            0.09   
2347    MAS                       Masco Corp  8359000000.00            0.09   
3051    PQG            Pq Group Holdings Inc  1608154000.00            0.09   
372     AWI   Armstrong World Industries Inc   975300000.00            0.09   
442    BCPC                       Balchem Cp   643679000.00            0.08   
1045     CX             Cemex S.A.B. DE C.V. 14125255102.04            0.08   
4108    WLK           Westlake Chemical Corp  8635000000.00            0.07   
4074   WDFC                   W D 40 Company   408518000.00            0.07   
677      CC                 Chemours Company  6638000000.00            0.07   
3267    RPM            RPM International Inc  5321643000.00            0.07   
386    AXTA       Axalta Coating Systems Ltd  4696000000.00            0.07   
2078    JHX       James Hardie Industries Se  2054500000.00            0.07   
1610    GGB                      Gerdau S.A. 11896772680.41            0.07   
3895    UFS                      Domtar Corp  5455000000.00            0.06   
3423    SID   Companhia Siderurgica Nacional  5919815721.65            0.06   
2183    KWR             Quaker Chemical Corp   867520000.00            0.06   
3541    SQM   Sociedad Quimica Y Minera S.A.  2265803000.00            0.05   
3923   UNVR                       Univar Inc  8632500000.00            0.05   
2629    NEU                   Newmarket Corp  2289675000.00            0.04   
3212   RGLD                   Royal Gold Inc   459042000.00            0.04   
2296    LPX           Louisiana-Pacific Corp  2828000000.00            0.03   
2392    MDU                Mdu Res Group Inc  4531552000.00            0.02   
3631    SXT       Sensient Technologies Corp  1386815000.00            0.02   
3470    SMG       Scotts Miracle-Gro Company  2663400000.00            0.01   
406     BAK                     Braskem S.A. 14948419072.16            0.00   
589     BTU              Peabody Energy Corp  5581800000.00            0.00   
3297    RYN                Rayonier Inc REIT   816138000.00           -0.00   
85      AEM           Agnico-Eagle Mines Ltd  2191221000.00           -0.02   
2887   PAAS             Pan Amer Silver Corp   784495000.00           -0.04   
1606    GFI                  Gold Fields Ltd  257780000

In [130]:
assets = mcap_grouped_data['Ticker'].to_list()

pf_data = pd.DataFrame()

for a in assets:
    pf_data[a] = wb.DataReader(a, data_source = 'yahoo', start = '2018-1-1')['Adj Close']

(pf_data / pf_data.iloc[0] * 100).plot()

In [2]:
lcap_gen = large_caps.groupby(['Sector']).__iter__()

NameError: name 'large_caps' is not defined

In [3]:
lcap_group_id, lcap_grouped_data = lcap_gen.__next__()
print(lcap_group_id) 
lcap_grouped_data.sort_values(by='Revenue Growth', ascending=False)

NameError: name 'lcap_gen' is not defined

In [1]:
assets = lcap_grouped_data['Ticker'].to_list()

pf_data = pd.DataFrame()

for a in assets:
    pf_data[a] = wb.DataReader(a, data_source = 'yahoo', start = '2018-1-1')['Adj Close']

(pf_data / pf_data.iloc[0] * 100).plot()

NameError: name 'lcap_grouped_data' is not defined

## Graphs and Visualizations

Count of Companies by Sector

In [ ]:
plt.figure(figsize=(18,8))
sns.countplot(x='Sector', data = df, palette='YlGnBu', order=df['Sector'].value_counts().index).set_xticklabels(labels = df['Sector'].value_counts().index, fontdict={'fontsize': 12},rotation=30)
plt.tight_layout()
# plt.savefig(os.path.join('Figures','StockVolume_Sector.png'))

Revenues by Sector

In [ ]:
sector_rev = pd.DataFrame(df.groupby(['Sector']).mean()['Revenue']).reset_index().sort_values(by='Revenue', ascending=False)

plt.figure(figsize=(18,8))
plt.title('Revenues by Sector')
sns.barplot(x = sector_rev['Sector'], y = sector_rev['Revenue'], palette='YlGnBu',).set_xticklabels(labels = sector_count['Sector'], fontdict={'fontsize': 12}, rotation=30)
plt.tight_layout();
# plt.savefig(os.path.join('Figures','StockVolume_Sector.png'))

Count of Companies across Market Cap Sizes

In [ ]:
plt.figure(figsize=(18,8))
sns.countplot(x='Market Cap Size', data = df, palette='YlGnBu', order=df['Market Cap Size'].value_counts().index).set_xticklabels(labels = df['Market Cap Size'].value_counts().index, fontdict={'fontsize': 12},rotation=30)
plt.tight_layout()
plt.ylabel('Company Count')
# plt.savefig(os.path.join('Figures','MarketCapBreakdown.png'))

In [ ]:
bars = []
sectors = df['Sector'].unique()
caps=['Small Cap', 'Mid Cap', 'Large Cap']
for sector in sectors:
    bars.append(go.Bar(name=sector, x=caps, y=np.array(df[df['Sector'] == sector]['Market Cap Size'].value_counts())))

plt.figure(figsize=(30,12))
fig = go.Figure(data=bars)
# Change the bar mode
fig.update_layout(barmode='stack')
fig.show()

In [ ]:
sns.pairplot(df, vars = ['2019 PRICE VAR [%]', 'R&D Expenses', 'SG&A Expense',], dropna = True, hue='Sector', palette='YlGnBu_d')

In [ ]:
df[cond].cov();

In [ ]:
corrs = df[cond].corr()

In [ ]:
plt.figure(figsize=(20,20))
g = sns.heatmap(corrs, center=0)

## Regression Analysis

In [ ]:
y = df["2019 PRICE VAR [%]"]

X = sm.add_constant(df[x['Indicator']].fillna(0))

reg = sm.OLS(y, X).fit()

reg.summary();

In [ ]:
# df.to_csv(os.path.join('2018_data.csv'))